In [ ]:
import sys
sys.path.append('/home/daylen/xgboost/python-package')

In [ ]:
import sklearn
from sklearn.ensemble import RandomForestClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.model_selection import RandomizedSearchCV
from sklearn import metrics
from sklearn import model_selection
from sklearn.utils import shuffle
from sklearn import svm
import numpy as np
import matplotlib.pyplot as plt
import itertools
import pandas
from sklearn_porter import Porter
from sklearn.externals import joblib
import xgboost as xgb
import time
# sudo apt-get install python-opencv
import cv2
import collections
%matplotlib inline

In [ ]:
xgb.__path__

In [ ]:
cv2.__version__

# Crosswalks

## Data Preprocessing


In [ ]:
% ll /mnt/flashblade/daylen/xwalk_v2_mining/*event_id*.csv

In [ ]:
FNAME_PREFIX = '/mnt/flashblade/daylen/xwalk_v2_mining/event_id'

In [ ]:
%%time
# train_data = pandas.read_csv(FNAME_PREFIX + '_train.csv')
test_data = pandas.read_csv(FNAME_PREFIX + '_test.csv')

In [ ]:
# print train_data['label'].value_counts()
print test_data['label'].value_counts()
# print 'baseline accuracy', float(sum(train_data['label'] == 'IN_LANE')) / train_data.shape[0]

In [ ]:
test_data['sample_type'].iloc[0]

In [ ]:
N=2000
count = 0
for i, row in test_data[test_data.sample_type=='positive_before'].filter(regex='velocity_mag').iterrows():
    plt.plot(row.values, 'b-', alpha=0.02)
    count+=1
    if count > N:
        break

In [ ]:
#train_data[train_data['label'] == 0]['true_distance9'].mean()
for sample_type in np.unique(train_data['sample_type']):
    print sample_type, train_data[train_data['sample_type'] == sample_type]['true_distance9'].mean()

In [ ]:
n_crossability = np.sum(train_data['crossable'] != 0) + np.sum(train_data['non_crossable'] != 0)
n_total = train_data.shape[0]
print n_crossability, n_total, n_crossability / float(n_total)


In [ ]:
print 'P(crossable | label=0)', np.mean(test_data[test_data['label'] == 1]['crossable'])
print 'P(non-crossable | label=0)', np.mean(test_data[test_data['label'] == 1]['non_crossable'])


In [ ]:
for category_name in np.unique(test_data.sample_type):
    plt.figure()
    frq, edges = np.histogram(test_data[test_data.sample_type == category_name].accel_mag9, bins=40, range=(0, 3))
    plt.bar(edges[:-1], frq, width=np.diff(edges), ec="k", align="edge")
    plt.xlabel('accel [m/s^2]')
    plt.ylabel('frequency')
    plt.title('ped accel ' + category_name)

In [ ]:
test_data.shape

In [ ]:
np.unique(test_data.event_key).shape

In [ ]:
def xy_split(samples):
    """
    splits row into x and y
    y can include metadata, it's not just the label
    """
    # TODO magic num
    METADATA_COLS = 3
    num_features = samples.shape[1] - METADATA_COLS
    print 'num features', num_features
    return samples.iloc[:,:num_features], samples.iloc[:,num_features:]

In [ ]:
%%time
# xtrain, ytrain = xy_split(train_data)
xtest, ytest = xy_split(test_data)

In [ ]:
# ytrain_encoded = ytrain['label'].as_matrix()
ytest_encoded = ytest['label'].as_matrix()

# opencv gradient boosted trees

In [ ]:
# evaluation helper functions
import progressbar

def accuracy(x, y):
    x_matrix = x.as_matrix().astype(np.float32)
    correct = 0
    bar = progressbar.ProgressBar()
    
    for i in bar(range(x_matrix.shape[0])):
        pred = gbtrees.predict(x_matrix[i])
        if pred == y[i]:
            correct += 1
    return float(correct) / x_matrix.shape[0]

def predict_all(x):
    x_matrix = x.as_matrix().astype(np.float32)
    preds = []
    bar = progressbar.ProgressBar()
    for i in bar(range(x_matrix.shape[0])):
        pred = gbtrees.predict(x_matrix[i])
        preds.append(pred)
    return preds



In [ ]:
# params

param_grid = sklearn.model_selection.ParameterGrid({
    'loss_function_type': [cv2.GBTREES_DEVIANCE_LOSS],
    'weak_count': [8],
    'shrinkage': [0.3],
    'subsample_portion': [1],
    'max_depth': [6],
    'use_surrogates': [False]
})

In [ ]:
%%time

# train
results = []
print len(param_grid)
for params in list(param_grid):
    start_t = time.time()
    print params
    gbtrees = cv2.GBTrees()
    gbtrees.train(xtrain.as_matrix().astype(np.float32), cv2.CV_ROW_SAMPLE, ytrain_encoded,
                params=params)
    test_acc = accuracy(xtest, ytest_encoded)
    print test_acc
    print 'took', time.time() - start_t, 'sec'
    print ''
    results.append((params, accuracy, time.time() - start_t))

In [ ]:
# save model
gbtrees.save('/home/daylen/ml_models/crosswalk_v3_b1.yaml')

In [ ]:
# load model

gbtrees = cv2.GBTrees()
gbtrees.load('/home/daylen/ml_models/crosswalk_v2_b6.yaml')

In [ ]:
# print accuracy(xtrain, ytrain_encoded)
# print accuracy(xtest, ytest_encoded)
ytrainpred = np.array(predict_all(xtrain))
ytestpred = np.array(predict_all(xtest))

In [ ]:

def predict_all_prob(x):
    x_matrix = x.as_matrix().astype(np.float32)
    all_probs = []
    bar = progressbar.ProgressBar()
    for i in bar(range(x_matrix.shape[0])):
        probs = []
        # TODO(daylen): this assumes the k are in order. Check the OpenCV yaml
        # file to see if this is really the case.
        for k in [0, 1]:
            prob = gbtrees.predict(x_matrix[i], k=k)
            probs.append(np.exp(prob))
        all_probs.append(probs)
    all_probs = np.array(all_probs)
    all_probs /= np.sum(all_probs, axis=1)[:,None]
    return all_probs
# ytrainpredproba = predict_all_prob(xtrain)[:,1]
ytestpredproba = predict_all_prob(xtest)[:,1]


## xgboost

In [ ]:
# Convert numpy to XGB buffer
dtrain = xgb.DMatrix(xtrain, label=ytrain_encoded)
dtest = xgb.DMatrix(xtest, label=ytest_encoded)
# dtrain.save_binary('/home/daylen/ml_data/xgb_train.buffer')
# dtest.save_binary('/home/daylen/ml_data/xgb_test.buffer')

In [ ]:
# Load XGB buffer
dtrain = xgb.DMatrix('/home/daylen/ml_data/xgb_train.buffer')
dtest = xgb.DMatrix('/home/daylen/ml_data/xgb_test.buffer')

In [ ]:
# Stats
print dtrain.get_label().mean()
print dtest.get_label().mean()

In [ ]:
%%time
# PARAM SEARCH
# params = {'tree_method': 'hist', 'objective': 'binary:logistic', 'max_depth': 6, 'eta': 0.3}

param_grid = sklearn.model_selection.ParameterGrid({
    'tree_method': ['hist'],
    'objective': ['binary:logistic'],
    'max_depth': [5, 6, 7, 8, 9],
    'eta': [0.1, 0.2, 0.3, 0.4],
})

evallist = [(dtest, 'test'), (dtrain, 'train')]
print 'Begin param search'
results = []
for n in [4, 8, 16, 32]:
    for params in param_grid:
        bst = xgb.train(params, dtrain, n, evallist)
        entry = (n, params, bst.eval(dtest))
        print entry
        results.append(entry)
        

In [ ]:
%%time
# SINGLE MODEL

params = {'tree_method': 'hist', 'objective': 'binary:logistic', 'max_depth': 6, 'eta': 0.3}


evallist = [(dtest, 'test'), (dtrain, 'train')]
print 'Begin train'
bst = xgb.train(params, dtrain, 8, evallist)
# entry = (32, params, bst.eval(dtest))
# print entry


In [ ]:
results2 = map(lambda x: (x[0], x[1], float(x[2][x[2].index(':')+1:])), results)
results2.sort(key=lambda x: x[2])

In [ ]:
results2[0:10]

In [ ]:
# Save model
bst.save_model('/home/daylen/ml_models/xgb_count_16_depth_12_n_6M_with_junction.model')

In [ ]:
# Load model
bst = xgb.Booster()
bst.load_model('/home/daylen/ml_models/xgb_count_16_depth_12_n_6M_with_junction.model')

In [ ]:
# Predict
ytrainpredproba = bst.predict(dtrain)
ytestpredproba = bst.predict(dtest)
ytrainpred = np.rint(ytrainpredproba)
ytestpred = np.rint(ytestpredproba)

In [ ]:
ytest

In [ ]:
from sklearn.metrics import confusion_matrix


def plot_confusion_matrix(cm, classes,
                          normalize=False,
                          title='Confusion matrix',
                          cmap=plt.cm.Blues):
    """
    This function prints and plots the confusion matrix.
    Normalization can be applied by setting `normalize=True`.
    """
    if normalize:
        cm = cm.astype('float') / cm.sum(axis=1)[:, np.newaxis]
        print("Normalized confusion matrix")
    else:
        print('Confusion matrix, without normalization')

    print(cm)

    plt.imshow(cm, interpolation='nearest', cmap=cmap)
    plt.title(title)
    plt.colorbar()
    tick_marks = np.arange(len(classes))
    plt.xticks(tick_marks, classes, rotation=45)
    plt.yticks(tick_marks, classes)

    fmt = '.2f' if normalize else 'd'
    thresh = cm.max() / 2.
    for i, j in itertools.product(range(cm.shape[0]), range(cm.shape[1])):
        plt.text(j, i, format(cm[i, j], fmt),
                 horizontalalignment="center",
                 color="white" if cm[i, j] > thresh else "black")

    plt.tight_layout()
    plt.ylabel('True label')
    plt.xlabel('Predicted label')

# Compute confusion matrix
cnf_matrix = confusion_matrix(ytest_encoded, ytestpredproba > 0.55)
np.set_printoptions(precision=2)

# Plot non-normalized confusion matrix
plt.figure()
plot_confusion_matrix(cnf_matrix, classes=['no cross', 'crossing'],
                      title='model v2_b1, thres 0.55')

plt.show()

## P/R curves


In [ ]:
np.savetxt('/mnt/flashblade/daylen/debug_pr_curve_labels.txt', ytest_encoded)

In [ ]:
np.savetxt('/mnt/flashblade/daylen/debug_pr_curve_preds.txt', ytestpredproba)

In [ ]:
from sklearn.metrics import precision_recall_curve
import matplotlib.pyplot as plt
from sklearn.metrics import average_precision_score

average_precision = average_precision_score(ytest_encoded, ytestpredproba)

print('Average precision-recall score: {0:0.2f}'.format(
      average_precision))

precision, recall, _ = precision_recall_curve(ytest_encoded, ytestpredproba)
plt.figure(figsize=(10, 7))
plt.step(recall, precision, color='b', alpha=0.2,
         where='post')
plt.fill_between(recall, precision, step='post', alpha=0.2,
                 color='b')

plt.xlabel('Recall')
plt.ylabel('Precision')
plt.ylim([0, 1.05])
plt.xlim([0, 1.03])
plt.title('2-class Precision-Recall curve: AP={0:0.2f}'.format(
          average_precision))

In [ ]:
# Performance per category
print 'TRAIN'
for category_name in np.unique(train_data.sample_type):
    idxs = ytrain.loc[ytrain.sample_type == category_name].index.tolist()
    print category_name, '=', sklearn.metrics.accuracy_score(ytrain_encoded[idxs], ytrainpred[idxs])
print 'TEST'
for category_name in np.unique(test_data.sample_type):
    idxs = ytest.loc[ytest.sample_type == category_name].index.tolist()
    print category_name, '=', sklearn.metrics.accuracy_score(ytest_encoded[idxs], ytestpred[idxs])


## Failure cases

In [ ]:
errors = np.absolute(ytestpredproba - ytest_encoded)
idxs = np.flip(np.argsort(errors), axis=0)
csv_rows = []
for idx in idxs[:5000]:
    event_id, ts = ytest.iloc[idx]['event_key'].split(':')
    csv_rows.append([ytestpredproba[idx], ytest.iloc[idx]['label'], event_id, ts])

import csv
with open('/mnt/flashblade/daylen/failure_cases.csv', 'w') as csvfile:
    writer = csv.writer(csvfile, delimiter=',')
    for row in csv_rows:
        writer.writerow(row)
